In [1]:
%%capture

import warnings

warnings.filterwarnings("ignore")
import calitp_data_analysis.magics

import geopandas as gpd
import pandas as pd

from great_tables import GT

import _report_utils
from update_vars import GTFS_DATA_DICT, RT_SCHED_GCS

SHARED_GCS = GTFS_DATA_DICT.gcs_paths.SHARED_GCS

In [2]:
import google.auth

credentials, project = google.auth.default()

import gcsfs

fs = gcsfs.GCSFileSystem()

In [3]:
# Comment out and leave this cell right below pandas
# district = "AD 03"

In [4]:
# Parameters
district = "AD 08"


In [5]:
legislative_crosswalk = pd.read_parquet(
    f"{SHARED_GCS}crosswalk_transit_operators_legislative_districts.parquet",
    filters = [[("legislative_district", "==", district)]]
)

def readable_district_name(word: str) -> str:
    if "SD" in word:
        return word.replace("SD", "Senate District")
    elif "AD" in word:
        return word.replace("AD", "Assembly District")

district_full_name = readable_district_name(district)

In [6]:
%%capture_parameters
district, district_full_name

In [7]:
# Read in all datasets here with GTFS_DATA_DICT 
# Reran merge_operator_data.py to test this
OPERATOR_FILE = GTFS_DATA_DICT.digest_tables.operator_profiles
OPERATOR_ROUTE = GTFS_DATA_DICT.digest_tables.operator_routes_map
operator_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_FILE}.parquet",
).merge(
    legislative_crosswalk,
    on = "name",
    how = "inner"
)

# using name instead of schedule_gtfs_dataset_key allows us to get 
# the last ones for LA Metro without keeping extraneous rows for LA Metro when keys changed
operator_df = operator_df.sort_values(
    ["service_date", "name"], 
    ascending=[False, True]
).drop_duplicates(
    subset=["name"]
).reset_index(drop=True)

# AD 08

These are district summaries for [GTFS Digest](https://gtfs-digest--cal-itp-data-analyses.netlify.app/). 

In [8]:
district_summary = _report_utils.district_stats(
    operator_df, 
    "legislative_district"
)

In [9]:
summary_table1 = (GT(
    district_summary.drop(
        columns = ["arrivals_per_stop", "trips_per_operator"]
    ).pipe(
        _report_utils.transpose_summary_stats, 
        district_col = "legislative_district"
    )
)
 .fmt_integer(columns="value")
 .cols_label(index="")
 .tab_header(title = f"{district_full_name} GTFS summary stats")
)

summary_table2 = (GT(
    district_summary[
        ["legislative_district", "arrivals_per_stop", "trips_per_operator"]
    ].pipe(
        _report_utils.transpose_summary_stats,
        district_col = "legislative_district"
    )
)
 .fmt_number("value", decimals=1)
 .cols_label(index="")
)

In [10]:
display(summary_table1)
display(summary_table2)

GT(_tbl_data=         index   Value
0  # Operators      12
1     # routes     343
2      # trips   3,601
3      # stops   3,612
4   # arrivals  86,341, _body=<great_tables._gt_data.Body object at 0x7c7ed297ce10>, _boxhead=Boxhead([ColInfo(var='index', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='left', column_width=None), ColInfo(var='Value', type=<ColInfoTypeEnum.default: 1>, column_label='Value', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c7f0b41f350>, _spanners=Spanners([]), _heading=Heading(title='Assembly District 08 GTFS summary stats', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c7f0b43d010>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c7edb24ecd0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_left_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_left_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), heading_background_color=OptionsInfo(scss=True, category='heading', type='value', value=None), heading_align=OptionsInfo(scss=True, category='heading', type='value', value='center'), heading_title_font_size=OptionsInfo(scss=True, category='heading', type='px', value='125%'), heading_title_font_weight=OptionsInfo(scss=True, category='heading', type='value', value='initial'), heading_subtitle_font_size=OptionsInfo(

GT(_tbl_data=                index   Value
0   Arrivals per Stop    23.9
1  Trips per Operator  300.08, _body=<great_tables._gt_data.Body object at 0x7c7ed2f9eed0>, _boxhead=Boxhead([ColInfo(var='index', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='left', column_width=None), ColInfo(var='Value', type=<ColInfoTypeEnum.default: 1>, column_label='Value', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c7f0b4410d0>, _spanners=Spanners([]), _heading=Heading(title=None, subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c7ed27a6610>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c7ed276fad0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_left_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_left_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), heading_background_color=OptionsInfo(scss=True, category='heading', type='value', value=None), heading_align=OptionsInfo(scss=True, category='heading', type='value', value='center'), heading_title_font_size=OptionsInfo(scss=True, category='heading', type='px', value='125%'), heading_title_font_weight=OptionsInfo(scss=True, category='heading', type='value', value='initial'), heading_subtitle_font_size=OptionsInfo(scss=True, category='heading', type='px', value='85%'), heading_subtitle_font_weight=

## GTFS Stats by Operator

In [11]:
operators_in_district = operator_df.schedule_gtfs_dataset_key.unique()

In [12]:
operator_route_gdf = gpd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_ROUTE}.parquet",
    storage_options={"token": credentials.token},
)

In [13]:
operator_route_gdf = operator_route_gdf.loc[
    operator_route_gdf.schedule_gtfs_dataset_key.isin(operators_in_district)
][["name", "service_date", "recent_combined_name", "geometry"]]

In [14]:
operator_route_gdf = operator_route_gdf.sort_values(
    ["service_date", "name", "recent_combined_name"], 
    ascending=[False, True, True]
).drop_duplicates(
    subset = ["name", "recent_combined_name"]
).drop(
    columns = ["service_date", "recent_combined_name"]
    # drop route because after the dissolve, all operator routes are combined
    # so route would hold only the first row's value
).dissolve(by = "name").reset_index().pipe(_report_utils.replace_column_names)


In [15]:
operator_route_gdf["Transit Operator"] = operator_route_gdf["Transit Operator"].str.replace(" Schedule", "")

In [16]:
try:
    operator_route_gdf.explore(
    "Transit Operator", 
    tiles = "CartoDB Positron",
    categorical=True,
    legend=True,
    legend_kwds = {
        "width": 200
    })
except:
    pass

In [17]:
shared_cols = ["organization_name", "name"]
exclude_cols = ["schedule_gtfs_dataset_key", "legislative_district",
                "organization_source_record_id", "service_date", 
                "primary_uza"]

gtfs_service_cols = [
    c for c in operator_df.columns 
    if "operator_" in c]

In [18]:
gtfs_table_df = operator_df[
    shared_cols + gtfs_service_cols
].pipe(_report_utils.replace_column_names)

In [19]:
string_cols = gtfs_table_df.select_dtypes(include="object").columns.tolist()

gtfs_table = (
    GT(gtfs_table_df.sort_values("# Trips", ascending=False))
    .fmt_integer(
        columns = [
            c for c in gtfs_table_df.columns if c not in 
         ["Operator Service Miles", "Avg Arrivals per Stop"]
            and (c not in string_cols)
        ])
    .fmt_number(
        columns = ["Operator Service Miles", "Avg Arrivals per Stop"], 
        decimals = 1)
    .data_color(
        columns=["# Trips", "Avg Arrivals per Stop"],
        palette=["white", "green"],
        na_color="lightgray")
    .tab_header(
         title = f"{district_full_name}",
         subtitle = "Daily GTFS schedule statistics by operator")
    .cols_align(columns = [c for c in gtfs_table_df.columns if c not in ["Organization", "Transit Operator"]],
        align="center")
    )

gtfs_table = _report_utils.great_table_formatting(gtfs_table)
gtfs_table

GT(_tbl_data=                                    Organization  \
5                                 City of Fresno   
3                                      Greyhound   
0                                         Amtrak   
9               Eastern Sierra Transit Authority   
11                        Yosemite National Park   
2                                 City of Clovis   
10                                City of Madera   
4             Fresno County Rural Transit Agency   
1                       Calaveras Transit Agency   
7                 Tuolumne County Transit Agency   
6                                  Madera County   
12                        Yosemite National Park   
8   Yosemite Area Regional Transportation System   
13                Tuolumne County Transit Agency   

                     Transit Operator  # Routes  # Trips  # Shapes  # Stops  \
5                     Fresno Schedule        18     1344        75     1510   
3                    Flixbus Schedule       222      871       759      888   
0                     Amtrak Schedule        59      587       131      509   
9             Eastern Sierra Schedule        11      218        27      138   
11   Yosemite Valley Shuttle Schedule         2      152         2       18   
2                     Clovis Schedule         3      108        13      133   
10              Madera Metro Schedule         4      104         8      100   
4              Fresno County Schedule         7       40        15       83   
1                  Calaveras Schedule         2       36         6       20   
7             Tuolumne Remix Schedule         3       34         4       84   
6   Madera County Connection Schedule         4       32        11       35   
12    Mariposa Grove Shuttle Schedule         1       31         1        2   
8                      YARTS Schedule         4       24        19       65   
13                  Tuolumne Schedule         3       20         3       27   

    # Arrivals  Operator Service Miles  Avg Arrivals per Stop  
5        63803                  224.87                  42.25  
3         5665                92107.85                   6.38  
0         4117                35028.54                   8.09  
9         3739                  635.71                  27.09  
11        1917                   18.92                 106.50  
2         3055                   33.67                  22.97  
10        1780                   37.16                  17.80  
4          283                  272.68                   3.41  
1          287                   61.78                  14.35  
7          815                   57.55                   9.70  
6          252                  149.29                   7.20  
12          62                    4.03                  31.00  
8          344                  399.36                   5.29  
13         222                   68.82                   8.22  , _body=<great_tables._gt_data.Body object at 0x7c7e7f13a390>, _boxhead=Boxhead([ColInfo(var='Organization', type=<ColInfoTypeEnum.default: 1>, column_label='Organization', column_align='left', column_width=None), ColInfo(var='Transit Operator', type=<ColInfoTypeEnum.default: 1>, column_label='Transit Operator', column_align='left', column_width=None), ColInfo(var='# Routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='# Trips', type=<ColInfoTypeEnum.default: 1>, column_label='# Trips', column_align='center', column_width=None), ColInfo(var='# Shapes', type=<ColInfoTypeEnum.default: 1>, column_label='# Shapes', column_align='center', column_width=None), ColInfo(var='# Stops', type=<ColInfoTypeEnum.default: 1>, column_label='# Stops', column_align='center', column_width=None), ColInfo(var='# Arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='# Arrivals', column_align='center', column_width=None), ColInfo(var='Operator Service Miles', type=<ColInfoTypeEnum.default: 1>